# Math 152: Intro to Mathematical Software
### 2017-03-10
### Kiran Kedlaya; University of California, San Diego
### adapted from lectures by William Stein, University of Washington

### **Lecture 25: Algebra and number theory (prep for cryptography): part 2**


Announcements:
- Guest lectures next week: 
  * Monday, March 13: Kartik Venkatram
  * Wednesday, March 15: Alina Bucur
- No sections on Monday, March 13.
- Office hours next week:
  * Zonglin: Thursday, March 16, 3:30-5:30 in APM 5748.
  * Me: Friday, March 17, 11-12 in APM 7202.
  * Peter: Friday, March 17, 12-1 and 3-4 in APM 6132.
- Next week's homework due Friday, March 17 at 8pm. Peer grading due Sunday, March 19 at 8pm.
  * The first half of this assignment is "normal" (number theory and cryptography).
  * The second half is freeform: create your own lecture! See the assignment for details.
- Please do your course evaluation (CAPE)! Evaluations close Monday, March 20 at 8am.
- HW1-6 grades are available on TritonEd, plus some attendance and peer grading scores. Remember, there is no final exam for this course.
- Regarding grade cutoffs: as a minimum, 90% will be at least an A-, 80% at least a B-, 70% at least a C-. However, I will lower the cutoffs if necessary to achieve a distribution comparable to other upper-division courses (e.g., under no circumstances will the A range include fewer than 20% of the class).

This might be useful: https://wiki.sagemath.org/quickref?action=AttachFile&do=get&target=quickref-nt.pdf

## Back to the Chinese remainder theorem


Last time, I demonstrated how to use the extended Euclidean algorithm to make the Chinese remainder theorem explicit. What was that function called again?

In [0]:
xkcd(217)

There is also a built-in command for this!

In [0]:
(a,b,m,n) = (5,7,10^25 - 11, 10^37 + 28)
x = crt(a,b,m,n); print(x)

In [0]:
(a,b), (x%m, x%n)

In [0]:
x = crt(3, 0, 6, 9); x

## Multiplicative order and primitive roots

Let $a,n$ be integers with $\gcd(a,n) = 1$. Using the extended Euclidean algorithm as above, one can find a multiplicative inverse of $a$ modulo $n$, i.e., a value $b$ such that $ab \equiv 1 \pmod{n}$. In fact, Sage will do this automatically.

In [0]:
a = 577
n = 6825
gcd(a,n)

In [0]:
mod(a,n)^(-1)

In [0]:
1/mod(a,n)

In [0]:
a.inverse_mod(n)

In [0]:
## Or if you prefer abstract algebra syntax:
R = IntegerModRing(n)
R(a)^(-1)

As a consequence of the existence of the multiplicative inverse, there always exists a positive integer $d$ such that $a^d \equiv 1 \pmod{n}$. (There must be two powers that coincide mod $n$, and we can cancel the powers of $a$ from one side.)

If $n$ is prime, the little Fermat theorem implies that $d = n-1$ always works (although it need not be the smallest such value; more on this in a moment). For general $n$, there is a generalization of the Fermat theorem due to Euler: we have $a^{\phi(n)} \equiv 1 \pmod{n}$ where
$\phi(n)$ denotes the *Euler phi function* (or *totient function*): if $n$ has prime factorization $p_1^{e_1} \times p_2^{e_2} \times \cdots$, then
\[
\phi(n) = (p_1 - 1)p_1^{e_1-1}(p_2-1)p_2^{e_2-1} \cdots.
\]
For those who know group theory: recall that this works because the residue classes mod $n$ which have no common factor with $n$ form a group under multiplication, and $\phi(n)$ is its order.

In [0]:
factor(561)
euler_phi(561)

In [0]:
list(factor(561))

In [0]:
for (d,e) in factor(561):
    print euler_phi(d), 560 % euler_phi(d) #Aha!

So now it makes sense to consider the *smallest* positive integer $d$ such that $a^d \equiv 1 \pmod{n}$. This integer must divide $\phi(n)$, otherwise the remainder of $\phi(n)$ mod $d$ would be an even smaller value. (Or use group theory!) This $d$ is called the *multiplicative order* of $a$ mod $n$.

In [0]:
for d in range(1, 17):
    print (d, multiplicative_order(mod(d,17)))

Important result: if $n$ is prime, then there is always at least one value of $a$ for which the multiplicative order of $a$ mod $n$ is equal to the maximum possible value $\phi(n) = n-1$. Any such $a$ is called a *primitive root* mod $n$; these are relevant for discrete logarithms, more on which later.

(Abstract algebra interpretation; if $n$ is prime, then $(\ZZ/n\ZZ)^*$ is a cyclic group!)

In [0]:
primitive_root?

In [0]:
primitive_root(17)

In [0]:
a = primitive_root(37); print(a)

In [0]:
l = [mod(a,37)^i for i in range(36)]
l.sort()
l

## Discrete logarithms

Let $p$ be a prime. Suppose that $a$ is a primitive root mod $p$. Then for any $m$ not divisible by $p$, the *discrete logarithm* of $m$ mod $p$, with respect to the base $a$, is the integer $g \in \{0,\dots,p-2\}$ such that $a^g \equiv m \pmod{p}$.

In [0]:
mod(2, 101)^19

In [0]:
mod(98,101).log(mod(2,101))

This looks straightforward enough, but it is actually *very difficult* to compute discrete logarithms! There is no obvious trick for this.

As a result, the function $g \mapsto a^g \pmod{p}$ is often treated as a *one-way function*: it is easy to compute but hard to invert. (This is a practical definition, not a formal mathematical one, because we (probably) cannot say for sure that it is *actually* hard to compute, as opposed to our merely being ignorant.)

In any case, the existence of one-way functions makes it feasible to have *public-key cryptography*, where everyone knows how to encrypt a message but only one person knows how to decrypt; or *public-key signature schemes*, where only one person knows to encrypt but everyone knows how to decrypt.

The difficulty of integer factorization behaves in a similar (but slightly more complicated) way: if $p,q$ are two prime numbers, then it is easy to form the product $pq$ but much harder to recover $p$ and $q$ from the product.

## Quadratic residues

For $n$ a positive integer, an integer $a$ is a *quadratic residue mod $n$* if there exists a perfect square congruent to $a$ modulo $n$.

For example, say $n = 7$. To test whether a perfect square is congruent to $a$ modulo $n$, we need only test $0^2, \dots, 6^2$. Their residues modulo $7$ are $0, 1, 4, 2, 2, 4, 1$.

In [0]:
quadratic_residues(107) # for any p, will include 0 and (p-1)/2 other values.

For $p$ an odd prime, the list of quadratic residues mod $p$ will include 0 plus $(p-1)/2$ other values. (If we run over $\{0,\dots,p-1\}$, no residue can occur more than twice: if $x^2 \equiv y^2 \pmod{p}$, then $(x+y)(x-y)$ is divisible by $p$, and so one of $x+y$ or $x-y$ must be.)

For $p$ an odd prime and $a$ not divisible by $p$, $a$ is a quadratic residue modulo $p$ if and only if its discrete logarithm (with respect to any base) is *even*.

The *Legendre symbol* $\left( \frac{a}{p} \right)$ is defined to be $0$ if $a \equiv 0 \pmod{p}$, $+1$ if $a$ is a nonzero quadratic residue modulo $p$, 
and $-1$ if $a$ is not a quadratic residue mod $p$. This symbol has the multiplicativity property:
\[
\left(  \frac{a}{p} \right) \left(  \frac{b}{p} \right) = \left( \frac{ab}{p} \right).
\]
(The less-than-obvious part is that the product of two quadratic nonresidues is a quadratic residue. This would fail if $p$ were not prime.)

In [0]:
legendre_symbol(5, 7)

In [0]:
p = next_prime(10^70)
%time
legendre_symbol(3, p) ## How is this feasible?? No way we are exhausting over all residue classes mod p!

The *law of quadratic reprocity* (originally proved by Gauss) states that if $p,q$ are distinct odd primes, then
\[
\left(  \frac{p}{q} \right) \left(  \frac{q}{p} \right) = (-1)^{(p-1)(q-1)/4}.
\]
That is, the two Legendre symbols agree if either $p$ or $q$ is congruent to 1 mod 4, and disagree if they are both congruent to 3 mod 4.

If $a$ is not prime, you can apply quadratic reciprocity by first factoring $a$. But this is not necessary: if one defines the *Kronecker symbol* to extend the Legendre symbol via the rule
\[
\left(  \frac{a}{b_1} \right) \left(  \frac{a}{b_2} \right) = \left( \frac{a}{b_2} \right),
\]
then the formula
\[
\left(  \frac{p}{q} \right) \left(  \frac{q}{p} \right) = (-1)^{(p-1)(q-1)/4}.
\]
extends to all odd positive integers $p,q$.

This still leaves the prime 2, but there is another formula of Gauss to handle this case:
\[
\left(  \frac{2}{p} \right) = (-1)^{(p-1)/8}.
\]
That is, if $p$ is an odd prime, then 2 is a quadratic residue mod $p$ if $p$ is congruent to 1 or 7 mod 8, and a quadratic nonresidue mod $p$ if $p$ is congruent to 3 or 5 mod 8.

Upshot: you can compute Legendre (and Kronecker) symbols quickly using a form of the Euclidean algorithm!

In [0]:
%time 
a = next_prime(10^31)
b = next_prime(10^32)
legendre_symbol(a, b)